In [1]:
import numpy as np
import pandas as pd
pd.options.display.max_colwidth = 100
# https://stackoverflow.com/questions/19699367/unicodedecodeerror-utf-8-codec-cant-decode-byte

In [12]:
import nltk
from nltk.tokenize import word_tokenize

In [15]:
from nltk.corpus import stopwords

In [18]:
from nltk.stem.snowball import SnowballStemmer
from nltk.stem import WordNetLemmatizer

In [21]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [22]:
from sklearn.base import TransformerMixin, BaseEstimator
from sklearn.pipeline import Pipeline

In [24]:
from sklearn.model_selection import train_test_split

In [ ]:
train_data = pd.read_csv("train.csv", encoding='ISO-8859-1')

In [2]:
train_data.head()

ItemID  Sentiment  \
0       1          0   
1       2          0   
2       3          1   
3       4          0   
4       5          0   

                                                                                         SentimentText  
0                                                             is so sad for my APL friend.............  
1                                                                     I missed the New Moon trailer...  
2                                                                              omg its already 7:30 :O  
3            .. Omgaga. Im sooo  im gunna CRy. I've been at this dentist since 11.. I was suposed 2...  
4                                                         i think mi bf is cheating on me!!!       T_T

In [3]:
# taking some random tweets to gain some more insights
rand_indexs = np.random.randint(1,len(train_data),50).tolist()
train_data["SentimentText"][rand_indexs]

21966                                                   @3fingaz LOL.. i KNOW... BEEN BUSY!  iM BACK THOUGH 
23683    @Abbie_xD Knew you would love them!  Im actually at the law school at the mo and just printed of...
56603    @Beadinbabe Mine too!! Had 3 grandaughters last nite. Toys everywhere.  They'll wait till tomorr...
71095    @BrentSpiner Why do @wilw and @levarburton have &quot;Verified Accounts&quot; and you don't? You...
74962                             @brydie_alison12 are you kidding me we had roast too!!  it was awsome. (Y)
57840                               @bdeterding dammit i did  well i kept getting booted off for some reason
41979                                      @andrewroden I had to smuggle it back up the 303 from Cornwall ! 
62572                                                                               @Blandiine_ yes yes yes 
80718    @charlesmoreland Living in a foreign kitchen sucks. We don't my usual spices, and nothing is whe...
54979              

# ANALYSING EMOTICONS

In [5]:
# We are gonna find what emoticons are used in our dataset
import re
tweets_text = train_data['SentimentText'].str.cat()
print("tweets_text = {}".format(tweets_text))
emos = set(re.findall(r" ([xX:;][-']?.) ",tweets_text))
print("emos = {}".format(emos))
emos_count = []
for emo in emos:
    emos_count.append((tweets_text.count(emo), emo))
sorted(emos_count,reverse=True)
print("emos_count = {}".format(emos_count))

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



emos_count = [(16, ':['), (34, 'x2'), (126, ":'("), (1, ':-x'), (245, '::'), (713, ';)'), (1339, 'x@'), (2, ':;'), (59, ':1'), (12, 'X1'), (109, 'xm'), (10, ':T'), (36, 'XT'), (16, ':-p'), (2, ':D'), (842, 'xo'), (9, ':I'), (9, ';]'), (117, 'xh'), (25, ':*'), (1, ":'["), (984, ';3'), (1, ':-]'), (3, ':-['), (27, 'Xo'), (1, 'x|'), (32, 'x:'), (31, 'x-'), (251, 'x.'), (65, 'XX'), (5, 'XL'), (58, ':]'), (1, ':-W'), (33, ';/'), (3, ':Z'), (2, ';-;'), (26, ':-P'), (1, ':('), (3, ':-s'), (185, ':O'), (6, 'X,'), (887, 'xp'), (5, ':?'), (35, 'x)'), (37, 'xk'), (32, ':\\'), (12, ':x'), (57, ':s'), (11, 'XS'), (13, ':-O'), (142, ':p'), (1162, 'xa'), (92, ':|'), (254, 'xD'), (3, ':E'), (1, "x'd"), (2, ':}'), (166, ';D'), (6, ':$'), (234, 'X '), (217, ';t'), (146, 'x3'), (7, ':-|'), (7, ';-('), (75, ';o'), (118, ':@'), (117, ':S'), (27, 'XP'), (209, ';s'), (44, ';;'), (2, "X's"), (11, ':l'), (5, ':-S'), (6, ':-o'), (431, ';I'), (14, 'XM'), (1, "x'D"), (38, ':-D'), (5, ':X'), (8, ':C'), (2, 'X-('),

In [7]:
tweets_text

'                     is so sad for my APL friend.............                   I missed the New Moon trailer...              omg its already 7:30 :O          .. Omgaga. Im sooo  im gunna CRy. I\'ve been at this dentist since 11.. I was suposed 2 just get a crown put on (30mins)...         i think mi bf is cheating on me!!!       T_T         or i just worry too much?               Juuuuuuuuuuuuuuuuussssst Chillin!!       Sunny Again        Work Tomorrow  :-|       TV Tonight      handed in my uniform today . i miss you already      hmmmm.... i wonder how she my number @-)      I must think about positive..      thanks to all the haters up in my face all day! 112-102      this weekend has sucked so far     jb isnt showing in australia any more!     ok thats it you win.    &lt;-------- This is the way i feel right now...    awhhe man.... I\'m completely useless rt now. Funny, all I can do is twitter. http://myloc.me/27HX    Feeling strangely fine. Now I\'m gonna go listen to some Semiso

# AIM IS TO SEGREGATE HAPPY AND SAD EMOTICONS

In [9]:
HAPPY_EMO = r" ([xX;:]-?[dD)]|:-?[\)]|[;:][pP]) "
SAD_EMO = r" (:'?[/|\(]) "
happy_emoticons = set(re.findall(HAPPY_EMO, tweets_text))
sad_emoticons = set(re.findall(SAD_EMO, tweets_text))
print("Happy emoticons: {}".format(happy_emoticons))
print("Sad emoticons: {}".format(sad_emoticons))

Happy emoticons: {':p', 'x)', ';-D', ';D', ':d', ';d', ';)', ':-D', ';-)', ';P', 'XD', ';p', 'xD', ':D', 'xd'}
Sad emoticons: {':/', ':(', ':|', ":'("}


In [11]:
len(happy_emoticons), len(sad_emoticons)

(15, 4)

In [13]:
#nltk.download('punkt')
def most_used_words(text):
    tokens = word_tokenize(text)
    frequency_dist = nltk.FreqDist(tokens)
    print("There is %d different words" % len(set(tokens)))
    return sorted(frequency_dist,key=frequency_dist.__getitem__, reverse=True)

In [14]:
most_used_words(train_data['SentimentText'].str.cat())[:100]

There is 133899 different words


['@',
 '!',
 '.',
 'I',
 ',',
 'to',
 'the',
 'you',
 '?',
 'a',
 'it',
 'i',
 '...',
 ';',
 'and',
 '&',
 'my',
 'for',
 'is',
 'that',
 "'s",
 "n't",
 'in',
 'of',
 'me',
 'have',
 'on',
 'quot',
 "'m",
 'so',
 ':',
 'but',
 '#',
 'do',
 'was',
 'be',
 'not',
 'your',
 'are',
 'just',
 'with',
 'like',
 '-',
 'at',
 'too',
 'get',
 'good',
 'u',
 'up',
 'know',
 'all',
 'this',
 'now',
 'no',
 'we',
 'out',
 ')',
 'love',
 'can',
 '(',
 'what',
 'one',
 'will',
 'lol',
 'go',
 'about',
 'did',
 "'ll",
 'got',
 'amp',
 'there',
 'day',
 'http',
 'see',
 "'re",
 'if',
 'time',
 'they',
 'think',
 'as',
 'when',
 'from',
 'You',
 'It',
 'going',
 'really',
 'am',
 'work',
 'well',
 'had',
 'would',
 'how',
 'he',
 'here',
 'some',
 'thanks',
 'back',
 'im',
 'haha',
 'or']

In [16]:
#nltk.download("stopwords")
mw = most_used_words(train_data['SentimentText'].str.cat())
most_words = []
for w in mw:
    if len(most_words) == 1000:
        break
    if w in stopwords.words("english"):
        continue
    else:
        most_words.append(w)

There is 133899 different words


In [17]:
sorted(most_words)

['!',
 '#',
 '$',
 '%',
 '&',
 "'",
 "'d",
 "'ll",
 "'m",
 "'re",
 "'s",
 "'ve",
 '(',
 ')',
 '*',
 '*hugs*',
 '*sigh*',
 '+',
 ',',
 '-',
 '--',
 '.',
 '..',
 '...',
 '/',
 '1',
 '10',
 '100',
 '12',
 '1st',
 '2',
 '20',
 '2nd',
 '3',
 '30',
 '30SECONDSTOMARS',
 '4',
 '5',
 '6',
 '7',
 '8',
 ':',
 ';',
 '=',
 '?',
 '@',
 'A',
 'AND',
 'Ah',
 'AlexAllTimeLow',
 'All',
 'Also',
 'Alyssa_Milano',
 'Am',
 'And',
 'Are',
 'As',
 'At',
 'Aw',
 'Awesome',
 'Aww',
 'Awww',
 'BSB',
 'Birthday',
 'But',
 'Ca',
 'Can',
 'Chris',
 'Come',
 'Congrats',
 'Cool',
 'D',
 'DM',
 'DO',
 'Damn',
 'Day',
 'Did',
 'Do',
 'Enjoy',
 'FF',
 'Follow',
 'FollowFriday',
 'For',
 'Friday',
 'Get',
 'Glad',
 'Go',
 'God',
 'Good',
 'Got',
 'Great',
 'Had',
 'Haha',
 'Happy',
 'Have',
 'He',
 'Hello',
 'Hey',
 'Hi',
 'Hope',
 'How',
 'I',
 'IS',
 'IT',
 'If',
 'Im',
 'In',
 'Is',
 'It',
 'Its',
 'July',
 'June',
 'Just',
 'Keep',
 'LA',
 'LMAO',
 'LOL',
 'LOVE',
 'Let',
 'Like',
 'Lol',
 'London',
 'Love',
 'ME',


## STEMMING

In [19]:
#nltk.download('wordnet')
def stem_tokenize(text):
    stemmer = SnowballStemmer("english")
    stemmer = WordNetLemmatizer()
    return [stemmer.lemmatize(token) for token in word_tokenize(text)]

def lemmatize_tokenize(text):
    lemmatizer = WordNetLemmatizer()
    return [lemmatizer.lemmatize(token) for token in word_tokenize(text)]

# DATA TRANSFORMATION

In [23]:
class TextPreProc(BaseEstimator,TransformerMixin):
    def __init__(self, use_mention=False):
        self.use_mention = use_mention
    
    def fit(self, X, y=None):
        return self
    
    def transform(self, X, y=None):
        # We can choose between keeping the mentions
        # or deleting them
        if self.use_mention:
            X = X.str.replace(r"@[a-zA-Z0-9_]* ", " @tags ")
        else:
            X = X.str.replace(r"@[a-zA-Z0-9_]* ", "")
            
        # Keeping only the word after the #
        X = X.str.replace("#", "")
        X = X.str.replace(r"[-\.\n]", "")
        # Removing HTML garbage
        X = X.str.replace(r"&\w+;", "")
        # Removing links
        X = X.str.replace(r"https?://\S*", "")
        # replace repeated letters with only two occurences
        # heeeelllloooo => heelloo
        X = X.str.replace(r"(.)\1+", r"\1\1")
        # mark emoticons as happy or sad
        X = X.str.replace(HAPPY_EMO, " happyemoticons ")
        X = X.str.replace(SAD_EMO, " sademoticons ")
        X = X.str.lower()
        return X

In [25]:
sentiments = train_data['Sentiment']
tweets = train_data['SentimentText']

# I get those parameters from the 'Fine tune the model' part
vectorizer = TfidfVectorizer(tokenizer=lemmatize_tokenize, ngram_range=(1,2))
pipeline = Pipeline([
    ('text_pre_processing', TextPreProc(use_mention=True)),
    ('vectorizer', vectorizer),
])
print(pipeline)

Pipeline(memory=None,
         steps=[('text_pre_processing', TextPreProc(use_mention=True)),
                ('vectorizer',
                 TfidfVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.float64'>,
                                 encoding='utf-8', input='content',
                                 lowercase=True, max_df=1.0, max_features=None,
                                 min_df=1, ngram_range=(1, 2), norm='l2',
                                 preprocessor=None, smooth_idf=True,
                                 stop_words=None, strip_accents=None,
                                 sublinear_tf=False,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=<function lemmatize_tokenize at 0x0000020368B69B88>,
                                 use_idf=True, vocabulary=None))],
         verbose=False)


In [26]:
# Splitting data into Test and train
learn_data, test_data, sentiments_learning, sentiments_test = train_test_split(tweets, sentiments, test_size=0.3)

# This will tranform our learning data from simple text to vector
# by going through the preprocessing tranformer.
learning_data = pipeline.fit_transform(learn_data)
print(learning_data)

  (0, 283090)	0.3317909502059632
  (0, 123102)	0.3317909502059632
  (0, 146882)	0.3317909502059632
  (0, 47572)	0.34395727970249285
  (0, 144703)	0.22748761762004532
  (0, 251760)	0.27200636850533666
  (0, 210823)	0.2404374344626562
  (0, 102213)	0.13022953594496098
  (0, 338636)	0.21870119735145369
  (0, 294602)	0.18266742532118552
  (0, 27259)	0.035528836675907886
  (0, 149121)	0.14249281499452954
  (0, 283063)	0.21801662331164176
  (0, 123004)	0.20184356946741058
  (0, 146872)	0.2564070579645521
  (0, 47427)	0.16493791255768459
  (0, 144585)	0.09910676946839911
  (0, 251554)	0.13773761907988863
  (0, 210149)	0.09600887190831876
  (0, 101948)	0.10741334326867316
  (0, 338526)	0.12209759871931194
  (0, 288770)	0.03552832134593678
  (0, 25874)	0.03500318878163532
  (1, 102589)	0.24298446985138275
  (1, 168307)	0.18474935541661353
  :	:
  (69990, 301099)	0.05267198596001031
  (69990, 341857)	0.09153979583489887
  (69990, 11766)	0.05252462969509898
  (69990, 24285)	0.06461876713318994
  

In [27]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import accuracy_score
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import BernoulliNB, MultinomialNB

lr = LogisticRegression()
bnb = BernoulliNB()
mnb = MultinomialNB()

models = {
    'logitic regression': lr,
    'bernoulliNB': bnb,
    'multinomialNB': mnb,
}

for model in models.keys():
    scores = cross_val_score(models[model], learning_data, sentiments_learning, scoring="f1", cv=10)
    print("===", model, "===")
    print("scores = ", scores)
    print("mean = ", scores.mean())
    print("variance = ", scores.var())
    models[model].fit(learning_data, sentiments_learning)
    print("score on the learning data (accuracy) = ", accuracy_score(models[model].predict(learning_data), sentiments_learning))
    print("")

C:\Users\Shubhi\Anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:940: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)
C:\Users\Shubhi\Anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:940: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-r

=== logitic regression ===
scores =  [0.80729292 0.81740388 0.81031352 0.80811538 0.81252989 0.80996132
 0.81673114 0.81231213 0.81001083 0.80972541]
mean =  0.8114396423496892
variance =  1.0220168592011264e-05


C:\Users\Shubhi\Anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:940: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


score on the learning data (accuracy) =  0.8701565893244942

=== bernoulliNB ===
scores =  [0.78017493 0.78696158 0.78864353 0.78774308 0.78565626 0.78373946
 0.79553729 0.78726852 0.78609062 0.78807792]
mean =  0.786989318013716
variance =  1.3721834271264813e-05
score on the learning data (accuracy) =  0.900702937478569

=== multinomialNB ===
scores =  [0.80111111 0.81217256 0.8087614  0.80972113 0.80843039 0.80900881
 0.81198485 0.80723962 0.80456965 0.80456459]
mean =  0.8077564113924149
variance =  1.0904514995452437e-05
score on the learning data (accuracy) =  0.8983740998971311



## HYPERPARAMETER TUNING

In [28]:
from sklearn.model_selection import GridSearchCV

grid_search_pipeline = Pipeline([
    ('text_pre_processing', TextPreProc()),
    ('vectorizer', TfidfVectorizer()),
    ('model', MultinomialNB()),
])

params = [
    {
        'text_pre_processing__use_mention': [True, False],
        'vectorizer__max_features': [1000, 2000, 5000, 10000, 20000, None],
        'vectorizer__ngram_range': [(1,1), (1,2)],
    },
]
grid_search = GridSearchCV(grid_search_pipeline, params, cv=5, scoring='f1')
grid_search.fit(learn_data, sentiments_learning)
print(grid_search.best_params_)

{'text_pre_processing__use_mention': True, 'vectorizer__max_features': None, 'vectorizer__ngram_range': (1, 2)}


# Going ahead with Multinomial 

In [29]:
mnb.fit(learning_data, sentiments_learning)

MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True)

In [30]:
testing_data = pipeline.transform(test_data)
mnb.score(testing_data, sentiments_test)

0.7584758475847585

## Prediction on Test data

In [32]:
sub_data = pd.read_csv("test.csv", encoding='ISO-8859-1')
sub_learning = pipeline.transform(sub_data.SentimentText)
sub = pd.DataFrame(sub_data.ItemID, columns=("ItemID", "Sentiment"))
sub["Sentiment"] = mnb.predict(sub_learning)
print(sub)

        ItemID  Sentiment
0            1          0
1            2          0
2            3          0
3            4          0
4            5          0
...        ...        ...
299984  299996          1
299985  299997          1
299986  299998          1
299987  299999          1
299988  300000          1

[299989 rows x 2 columns]


In [ ]:
model = MultinomialNB()
model.fit(learning_data, sentiments_learning)
tweet = pd.Series([input(),])
tweet = pipeline.transform(tweet)
proba = model.predict_proba(tweet)[0]
print("The probability that this tweet is sad is:", proba[0])
print("The probability that this tweet is happy is:", proba[1])